# Libraries and useful functions

In [2]:
#General
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import datetime
import time
import calendar
import re
import os
import sys
import json

import math
from statistics import variance, median, StatisticsError
from scipy.stats import f as F



#sklearn
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import AdaBoostClassifier

#NLP
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

ps = PorterStemmer()
wnl = WordNetLemmatizer()
stop_words = set(stopwords.words('english'))

#Neural Network
import tensorflow as tf
from tensorflow import keras
import torch
from transformers import BertTokenizer, BertForSequenceClassification, AutoTokenizer
from transformers import RobertaForSequenceClassification, RobertaTokenizer

#Others
import snscrape.modules.twitter as sntwitter 
import snscrape.base 
    
sys.path.insert(0, "C://Users/chun_/GisPy/gispy")

In [8]:
sentiModel = BertForSequenceClassification.from_pretrained("bert-senti")
sentiTokenizer = AutoTokenizer.from_pretrained("bert-senti")

def appendSentimentScore(data,targetCol, fileName):
    
    sentiList = []
    targetPrefix = "senti"
    targetFile = "data/dynamic/" + targetPrefix + "_" + fileName + ".csv"
    
    if os.path.isfile(targetFile):
        sentiList = pd.read_csv(targetFile)
        return pd.concat([data, sentiList], axis = 1)
    
    for i in data[targetCol]:
        inputs = sentiTokenizer(i, return_tensors="pt", truncation=True)
        result = sentiModel(**inputs).logits.tolist()[0]
        sentiList.append([math.exp(i)/sum([math.exp(i) for i in result]) for i in result]) 
        
    sentiList = pd.DataFrame(sentiList, columns = ["sentiment_" + str(i+1) for i in range(5)])
    sentiList.to_csv(targetFile, index=False)
            
    return pd.concat([data, sentiList], axis = 1)

In [9]:
arouModel = RobertaForSequenceClassification.from_pretrained("arousal-english-distilbroberta-base")
arouTokenizer = RobertaTokenizer.from_pretrained("arousal-english-distilbroberta-base")

def appendArousalScore(data,targetCol, fileName):
    
    arouList = []
    targetPrefix = "roberta_arousal"
    targetFile = "data/dynamic/" + targetPrefix + "_" + fileName + ".csv"
    
    if os.path.isfile(targetFile):
        arouList = pd.read_csv(targetFile)
        return pd.concat([data, arouList], axis = 1)
    
    for i in data[targetCol]:
        inputs = arouTokenizer(i, return_tensors="pt", truncation=True)
        result = arouModel(**inputs).logits.tolist()[0][0]
        arouList.append(result) 
        
    arouList = pd.DataFrame(arouList, columns = ["roberta_arousal"])
    arouList.to_csv(targetFile, index=False)
            
    return pd.concat([data, arouList], axis = 1)

In [10]:
dominModel = RobertaForSequenceClassification.from_pretrained("dominance-english-distilroberta-base")
dominTokenizer = RobertaTokenizer.from_pretrained("dominance-english-distilroberta-base")

def appendDominanceScore(data,targetCol, fileName):
    # count = 0
    dominList = []
    targetPrefix = "roberta_dominance"
    targetFile = "data/dynamic/" + targetPrefix + "_" + fileName + ".csv"
    
    if os.path.isfile(targetFile):
        dominList = pd.read_csv(targetFile)
        return pd.concat([data, dominList], axis = 1)
    
    for i in data[targetCol]:
        inputs = dominTokenizer(i, return_tensors="pt", truncation=True)
        result = dominModel(**inputs).logits.tolist()[0][0]
        dominList.append(result) 
        
    dominList = pd.DataFrame(dominList, columns = ["roberta_dominance"])
    dominList.to_csv(targetFile, index=False)
            
    return pd.concat([data, dominList], axis = 1)

In [11]:
concrModel = RobertaForSequenceClassification.from_pretrained("concreteness-english-distilroberta-base")
concrTokenizer = RobertaTokenizer.from_pretrained("concreteness-english-distilroberta-base")

def appendConcretenessScore(data,targetCol, fileName):
    # count = 0
    concrList = []
    targetPrefix = "roberta_concreteness"
    targetFile = "data/dynamic/" + targetPrefix + "_" + fileName + ".csv"
    
    if os.path.isfile(targetFile):
        concrList = pd.read_csv(targetFile)
        return pd.concat([data, concrList], axis = 1)
    
    for i in data[targetCol]:
        inputs = concrTokenizer(i, return_tensors="pt", truncation=True)
        result = concrModel(**inputs).logits.tolist()[0]
        concrList.append(np.exp(result[1]) / (np.sum(np.exp(result)))) 
        
    concrList = pd.DataFrame(concrList, columns = ["roberta_concreteness"])
    concrList.to_csv(targetFile, index=False)
            
    return pd.concat([data, concrList], axis = 1)

In [64]:
covidrumor = pd.read_csv("data/covidRumor/Twitter.csv")
covidrumor = appendConcretenessScore(covidrumor,"content", "covidRumor")

covidrumor

No. label                                            content  \
0        1     F  If you can hold your breath without coughing, ...   
1        2     F  A homemade hand sanitizer made with Tito's Vod...   
2        3     F  Gargling with salt water or Vinegar 'eliminate...   
3        4     U  Patients should avoid taking ibuprofen to reli...   
4        5     F  Chinese officials are seeking approval to star...   
...    ...   ...                                                ...   
2700  2709     F  telecommunications services in the country wil...   
2701  2710     F  Gov. Steve Sisolak's activation of the Guard t...   
2702  2711     F                   An officer died from coronavirus   
2703  2712     F  National Guard is being mobilized for anything...   
2704  2713     T  Thank you for your leadership Mayor Lucas! My ...   

                   source sentiment  reply numbers  retweet numbers  \
0      850196512341262036         3            2.0             61.0   
1     8081445194953918218         3            3.0             41.0   
2     1803907737236930232         3            6.0             39.0   
3     1989310298994352163         3            0.0              0.0   
4     6967004759672387621         4            0.0              0.0   
...                   ...       ...            ...              ...   
2700  8183648438884397934         3            3.0              4.0   
2701  4396957800986667223         3            1.0              4.0   
2702  6356967677817419212         2            0.0              1.0   
2703  3111348880049192737         3            1.0              5.0   
2704  3418545398543234785   #VALUE!            0.0              3.0   

      likes numbers  Unnamed: 0  roberta_concreteness  
0              95.0           0              0.767205  
1              67.0           1              0.950578  
2              73.0           2              0.922278  
3               0.0           3              0.878569  
4               0.0           4              0.879505  
...             ...         ...                   ...  
2700            7.0        2700              0.897537  
2701            3.0        2701              0.604245  
2702            8.0        2702              0.953978  
2703            5.0        2703              0.567337  
2704           12.0        2704              0.449345  

[2705 rows x 10 columns]

In [2]:
concrModel = RobertaForSequenceClassification.from_pretrained("concreteness-english-distilroberta-base")
concrTokenizer = RobertaTokenizer.from_pretrained("concreteness-english-distilroberta-base")

In [4]:
inputs = concrTokenizer("computer", return_tensors="pt", truncation=True)
result = concrModel(**inputs).logits.tolist()[0]
# print("Raw Result: " + str(result))
# print("Softmax-ed Result: "  + str([math.exp(i)/sum([math.exp(i) for i in result]) for i in result]))
np.exp(result[1]) / (np.sum(np.exp(result)))

0.9873110102907772

In [61]:
inputs = arouTokenizer(test, return_tensors="pt", truncation=True)
result = arouModel(**inputs).logits.tolist()[0][0]
result

0.41491782665252686

In [12]:
vad = pd.read_csv("data/misc/BRM-emot-submit.csv", index_col = 1)
freq = pd.read_csv("data/misc/unigram_freq.csv")

In [13]:
def tk(text):
    return word_tokenize(re.sub(r'[^\w\s]', '', str(text).lower())) 

def stopword(tokens):
    result = []
    for w in tokens:
        if w not in stop_words:
            result.append(w)
    return result

def lemma(tokens):
    result = []

    for token in tokens:
        stemmed_word = wnl.lemmatize(token)
        result.append(stemmed_word)
    return result


In [6]:
stopword(["is", "of", "Of","1"])

['Of', '1']

In [14]:
def valence(tokens):
    
    count = 0
    result = 0
    
    for token in tokens:
        try:
            valence = vad["V.Mean.Sum"][token]
            result += valence
            count += 1
        except KeyError:
            continue
            
    if count > 0:
        return result/count
    return 5

def arousal(tokens):
    
    count = 0
    result = 0
    
    for token in tokens:
        try:
            arousal = vad["A.Mean.Sum"][token]
            result += arousal
            count += 1
        except KeyError:
            continue
            
    if count > 0:
        return result/count
    return 5

def dominance(tokens):
    
    count = 0
    result = 0
    
    for token in tokens:
        try:
            dominance = vad["D.Mean.Sum"][token]
            result += dominance
            count += 1
        except KeyError:
            continue
            
    if count > 0:
        return result/count
    return 5


def appendVAD(data,targetCol, fileName):
    
    targetPrefix = "VADScore_"
    targetFile = "data/dynamic/" + targetPrefix + "_" + fileName + ".csv"
    
    if os.path.isfile(targetFile):
        VADList = pd.read_csv(targetFile)
        return pd.concat([data, VADList], axis = 1)
    
    Valence = []
    for i in range(len(data)):
        Valence.append(valence(lemma(stopword(tk(data[targetCol][i]))))) 
    Valence = pd.DataFrame(Valence, columns = ["valence"])

    Arousal = []
    for i in range(len(data)):
        Arousal.append(arousal(lemma(stopword(tk(data[targetCol][i]))))) 
    Arousal = pd.DataFrame(Arousal, columns = ["arousal"])
    
    Dominance = []
    for i in range(len(data)):
        Dominance.append(dominance(lemma(stopword(tk(data[targetCol][i]))))) 
    Dominance = pd.DataFrame(Dominance, columns = ["dominance"])
    
    
    VADList = pd.concat([Valence, Arousal, Dominance], axis = 1)
    VADList.to_csv(targetFile, index=False)
    
    
    
    return pd.concat([data, VADList], axis = 1)
    

## Word Frequencies

In [15]:
freq = pd.read_csv("data/misc/unigram_freq.csv", index_col = 0).reset_index().reset_index()
freq["index"] = freq["index"] + 1
rankDict = freq.set_index("word", drop=True).to_dict()["index"]
freqDict = pd.read_csv("data/misc/unigram_freq.csv", index_col = 0).to_dict()["count"]

def appendFrequency(data,targetCol, fileName):
    #Max, Median, Median (Content Word), Min (Content Word)
    
    targetPrefix = "wordFreq_"
    targetFile = "data/dynamic/" + targetPrefix + "_" + fileName + ".csv"
    
    if os.path.isfile(targetFile):
        df = pd.read_csv(targetFile)
        return pd.concat([data, df], axis = 1)
    
    df = pd.DataFrame()
    
    
    #Max
    x = []
    for i in data[targetCol]:
        tokens = tk(i)
        v = -1
        for j in tokens:
            try:
                if rankDict[j] > v:
                    v = rankDict[j] 
            except KeyError:
                continue
        x.append(v)
    x = pd.DataFrame(x, columns = ["MaxRank"])
        
    df = pd.concat([df, x], axis = 1)
    
    #Median
    x = []
    for i in data[targetCol]:
        tokens = tk(i)
        v = []
        for j in tokens:
            try:
                v.append(rankDict[j])
            except KeyError:
                continue
        try:
            x.append(median(v))
        except StatisticsError:
            x.append(-1)
    x = pd.DataFrame(x, columns = ["MedianRank"])
        
    df = pd.concat([df, x], axis = 1)
    
    
    #Median
    x = []
    for i in data[targetCol]:
        tokens = stopword(tk(i))
        v = []
        for j in tokens:
            try:
                v.append(rankDict[j])
            except KeyError:
                continue
        try:
            x.append(median(v))
        except StatisticsError:
            x.append(-1)
    x = pd.DataFrame(x, columns = ["MedianContentRank"])
        
    df = pd.concat([df, x], axis = 1)
    
    
    #Min
    x = []
    for i in data[targetCol]:
        tokens = stopword(tk(i))
        v = 999999
        for j in tokens:
            try:
                if rankDict[j] < v:
                    v = rankDict[j]
            except KeyError:
                continue
        x.append(v)
    x = pd.DataFrame(x, columns = ["MinContentRank"])
        
    df = pd.concat([df, x], axis = 1)
    
    df.to_csv(targetFile, index=False)
    
    return pd.concat([data, df], axis = 1)
    

## GisPy

In [16]:
def emptyDocument():
    target = "C://Users/chun_/GisPy/data/documents"
    for filename in os.listdir(target):
        os.remove(target + "/" + filename)

def AddDocumentTofolder(df, prefix):
    
    target = "C://Users/chun_/GisPy/data/documents"
    count = 0
    
    for content in df:
        with open( target + "/" + prefix + "_" + str(count) + ".txt", "w", encoding="utf-8") as outfile:
            outfile.write(content)
        count += 1

emptyDocument()
# AddDocumentTofolder(pd.read_csv("data/covidRumor/Twitter.csv")["content"], "covidRumor")
# AddDocumentTofolder(pd.read_csv("data/preprocessed/officalComm.csv")["rawContent"], "offComm")
# AddDocumentTofolder(pd.read_csv("data/constraintAAAI/Constraint_Train.csv")["tweet"], "constraintAAAI")
AddDocumentTofolder(pd.read_csv("data/preprocessed/coaid_NoFeature.csv")["rawContent"], "coaid")

In [16]:
def appendGisPyData(data,fileName):
    
    gisPyResult = pd.DataFrame([])
    directory = "data/dynamic/gispy/"
    
    for filename in os.listdir(directory):
        f = os.path.join(directory, filename)
        if os.path.isfile(f):
            appendResult = pd.read_csv(f)
            appendResult = appendResult[appendResult["d_id"].str.contains("^" + fileName +"_")].reset_index()
            gisPyResult = pd.concat([gisPyResult, appendResult]) ##

    for i in range(len(gisPyResult)):
        gisPyResult["d_id"][i] = re.sub("^" + fileName +"_", "" ,gisPyResult["d_id"][i])
        gisPyResult["d_id"][i] = re.sub(".txt*","",gisPyResult["d_id"][i])
        gisPyResult["d_id"][i] = int(gisPyResult["d_id"][i])
    gisPyResult = gisPyResult.set_index("d_id").drop(["index","text"], axis = 1).sort_index()
    return pd.concat([data,gisPyResult], axis = 1)

In [47]:
b = subResult.set_index("d_id").drop(["index","text"], axis = 1).sort_index()

In [51]:
a = pd.read_csv("data/preprocessed/officalCommFiltered.csv")


id          date  \
0      1245440971896168448  1.585742e+09   
1      1245760292073672704  1.585819e+09   
2      1246075233208897544  1.585894e+09   
3      1246119052105453570  1.585904e+09   
4      1246203407674810368  1.585924e+09   
...                    ...           ...   
25176  1573676156255055872  1.664000e+09   
25177  1574003355604717570  1.664078e+09   
25178  1574694879430582273  1.664243e+09   
25179  1575102455364591616  1.664340e+09   
25180  1575392480773693441  1.664409e+09   

                                              rawContent  replyCount  \
0      Retirement community staff: Lower the chances ...           5   
1      The right message at the right time from the r...           9   
2      Everyone can help prevent spread of #COVID19. ...           3   
3      Do you have a loved one in a nursing home or a...           5   
4      #CareForEachOther by lending an ear (from a sa...           3   
...                                                  ...         ...   
25176  What does it mean when #polio virus is detecte...          64   
25177  If you plan to attend the @FIFAWorldCup in #Qa...          49   
25178  Second round of public hearings towards a #Pan...          32   
25179  This year, #WorldRabiesDay, let us bring toget...          49   
25180  🔴LIVE NOW - The second round of public hearing...          24   

       retweetCount  likeCount lang  source  sourceLabel  viewCount  ...  \
0                32         38   en     NaN          NaN        NaN  ...   
1                42         67   en     NaN          NaN        NaN  ...   
2                61         70   en     NaN          NaN        NaN  ...   
3                37         48   en     NaN          NaN        NaN  ...   
4                23         43   en     NaN          NaN        NaN  ...   
...             ...        ...  ...     ...          ...        ...  ...   
25176           101        280   en     NaN          NaN        NaN  ...   
25177            51        153   en     NaN          NaN        NaN  ...   
25178            56        136   en     NaN          NaN        NaN  ...   
25179           170        467   en     NaN          NaN        NaN  ...   
25180            35         99   en     NaN          NaN        NaN  ...   

       zSMCAUSwn_1p_binary  zSMCAUSwn_ap_binary  zSMCAUSwn_1_binary  \
0                -0.239914            -0.315127           -0.318678   
1                 0.852685             0.154715           -0.318678   
2                 0.442960             0.037254           -0.318678   
3                -0.239914             0.671541           -0.318678   
4                -0.239914            -0.315127           -0.318678   
...                    ...                  ...                 ...   
25176            -0.239914            -0.315127           -0.318678   
25177            -0.239914            -0.315127           -0.318678   
25178            -0.239914            -0.315127           -0.318678   
25179            -0.239914            -0.315127            1.102188   
25180            -0.239914            -0.315127           -0.318678   

      zSMCAUSwn_a_binary zPCCNC_megahr  zWRDIMGc_megahr  zPCCNC_mrc  \
0              -0.391433      0.517096        -0.105709    0.572541   
1               0.003567     -0.362344         0.208163    1.283026   
2              -0.095183     -0.238305         0.519849    0.524786   
3               0.438067      0.091631         0.221422    0.406026   
4              -0.391433      0.445218         0.701789    1.064250   
...                  ...           ...              ...         ...   
25176          -0.391433      0.713720         1.237690    1.176605   
25177          -0.391433     -0.854849        -0.636237    0.631069   
25178          -0.391433     -0.776861        -0.765111    0.031456   
25179           0.161567      0.224857         0.552175    0.107672   
25180          -0.391433     -0.118482        -0.416941    1.048356   

       zWRD

In [44]:
import stanza
stanza.install_corenlp()

2023-06-29 21:06:02 INFO: Installing CoreNLP package into C:\Users\chun_\stanza_corenlp...


# Hydrating Official Communication

In [3]:
def getUserLink(tweet):
    try:
        return tweet.user.link.url
    except AttributeError:
        return None

def tweetToDict(tweet):
    return {
            "id": tweet.id,
            "date": time.mktime(tweet.date.timetuple()), 
            "rawContent": tweet.rawContent,
            "replyCount": tweet.replyCount,
            "retweetCount": tweet.retweetCount,
            "likeCount": tweet.likeCount,
            "lang": tweet.lang,
            "source": tweet.source,
            "sourceLabel": tweet.sourceLabel,
            "viewCount": tweet.viewCount,
            "bookmarkCount": tweet.bookmarkCount,
            "pinned": tweet.pinned,

            "userId": tweet.user.id,
            "userDisplayName": tweet.user.displayname,
            "userRawDescription": tweet.user.rawDescription,
            "userVerified": tweet.user.verified,
            "userCreated": time.mktime(tweet.user.created.timetuple()),
            "userFollowersCount": tweet.user.followersCount,
            "userFriendsCount": tweet.user.friendsCount,
            "userStatusesCount": tweet.user.statusesCount,
            "userFavouritesCount": tweet.user.favouritesCount,
            "userListedCount": tweet.user.listedCount,
            "userMediaCount": tweet.user.mediaCount,
            "userLocation": tweet.user.location,
            "userProtected": tweet.user.protected,
            "userLink": getUserLink(tweet),
            "userBlue": tweet.user.blue,
            "userBlueType": tweet.user.blueType}


def saveTweet(directory, tweet):
    # with open("../../../Documents/PS928Local/testHydrated/1233160497756807172.json", "w") as outfile:
    with open( directory + str(tweet["id"]) + ".json", "w") as outfile:
        outfile.write(json.dumps(tweet))
        
def savePlaceholder(directory, fileName, text = "failed"):
    with open( directory + fileName, "w") as outfile:
        outfile.write(text)
        
def isTweetHydrated(directory, id):
    return os.path.exists(directory + str(id) + ".json")


def hydrateTweets(tweetList, directory, directoryIfFailed, retryFailed = False, batch = 1, pointer = 0):
    
    while pointer < len(tweetList):
        if isTweetHydrated(directoryIfFailed, tweetList[pointer]):
            print("Tweet hydration failed previously: " + str(tweetList[pointer]))
            if not retryFailed:
                pointer += batch
                continue

        if (not isTweetHydrated(directory, tweetList[pointer])):
            tweets = sntwitter.TwitterTweetScraper(tweetList[pointer])
            try:
                for i in tweets.get_items():
                    if type(i) != sntwitter.Tombstone:
                        thisTweet = tweetToDict(i)
                        saveTweet(directory, thisTweet)
                    else:
                        print("Note: Tweets Deleted for" + str(tweetList[pointer]))
                        savePlaceholder(directoryIfFailed, str(tweetList[pointer]) + ".json", "Deleted")
            except snscrape.base.ScraperException:
                print("Note: Tweets Result Error for" + str(tweetList[pointer]))
                savePlaceholder(directoryIfFailed, str(tweetList[pointer]) + ".json", "Not Scraped")
            except KeyError: # Some are deleted, rest are mostly politicians/news
                print("KeyError: " + str(tweetList[pointer]))
                savePlaceholder(directoryIfFailed, str(tweetList[pointer]) + ".json", "Unknown Key Error")
        else:
            print("Tweet already Hydrated: " + str(tweetList[pointer]))
        pointer += batch
        
        
def hydrateQuery(query, directory, directoryIfFailed = None, retryFailed = False):
    tweets = sntwitter.TwitterSearchScraper(query)
    for i in tweets.get_items():
        thisTweet = tweetToDict(i)
        saveTweet(directory, thisTweet)
        
        
def fetchOfficialCommunication(handle):
    month = 12
    year = 2019
    if not os.path.exists("../../../Documents/PS928Local/officalcomm/" + handle):
        os.makedirs("../../../Documents/PS928Local/officalcomm/" + handle)
        
    formatDate = datetime.date(year,month,1).strftime("%b%y")
    targetDir = "../../../Documents/PS928Local/officalcomm/" + handle + "/" + formatDate
    if not os.path.exists(targetDir):
        os.makedirs(targetDir)
        
    formateStart = str(year) + "-" + datetime.date(year,month,1).strftime("%m") + "-01"
    formateEnd = str(year) + "-" + datetime.date(year,month,1).strftime("%m") + "-" + str(calendar.monthrange(year, month)[1])
    query = "(from:" + handle + ") until:" + formateEnd +" since:" + formateStart +" -filter:replies"
    hydrateQuery(query, targetDir+ "/")
    
    for year in range(2020,2023):
        for month in range(1,13):
            formatDate = datetime.date(year,month,1).strftime("%b%y")
            targetDir = "../../../Documents/PS928Local/officalcomm/" + handle + "/" + formatDate
            if not os.path.exists(targetDir):
                os.makedirs(targetDir)
            
            formateStart = str(year) + "-" + datetime.date(year,month,1).strftime("%m") + "-01"
            formateEnd = str(year) + "-" + datetime.date(year,month,1).strftime("%m") + "-" + str(calendar.monthrange(year, month)[1])
            query = "(from:" + handle + ") until:" + formateEnd +" since:" + formateStart +" -filter:replies"
            hydrateQuery(query, targetDir + "/")
    
        

In [4]:
# fetchOfficialCommunication("WHO") #Done
# fetchOfficialCommunication("NHSEngland") #Done
# fetchOfficialCommunication("NHSuk") #Done
# fetchOfficialCommunication("UNICEF") #Done
# fetchOfficialCommunication("UN") #Done
# fetchOfficialCommunication("ECDC_EU") #Done
# fetchOfficialCommunication("EU_Commission") #Done
# fetchOfficialCommunication("CDCgov") #Done
# fetchOfficialCommunication("CDCemergency") #Done
# fetchOfficialCommunication("CDCGlobal") #Done
# fetchOfficialCommunication("HHSGov") #Done
# fetchOfficialCommunication("DHSCgovuk") #Done
# fetchOfficialCommunication("PHE_uk") #Done


@WHO
@NHSEngland
@NHSuk
@UNICEF
@UN
@ECDC_EU
@EU_Commission
@CDCgov
@CDCemergency
@CDCGlobal
@HHSGov
@DHSCgovuk
@PHE_uk

Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping a

Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages
Stopping after 20 empty pages


# Preprocess Data of Official Communication
The following tasks is done:
- filter those that are coronavirus related with regular expression: ".\*(covid|corona|demic|quarantin).*"
- only English tweets are retained
- sentiment score from BERT is added

In [51]:
def compileHydratedData(directory):
    returnValue = pd.DataFrame()
    for filename in os.listdir(directory):
        f = os.path.join(directory, filename)
        if os.path.isdir(f):
            returnValue = pd.concat([returnValue, compileHydratedData(f)]) ##
        else:
            jsonDict = json.load(open(f))
            returnValue = pd.concat([returnValue, pd.DataFrame([[jsonDict[i] for i in jsonDict]], columns = [i for i in jsonDict]) ])
    return returnValue

offcomm = compileHydratedData("data\\officalcomm").reset_index(drop=True)

def isCovidRelated(text):
    return len(re.findall((".*(covid|corona|demic|quarantin| case| test|virus|vaccin|spread).*"), text.lower())) > 0

#filter
ind = offcomm["rawContent"].apply(isCovidRelated)
offcomm = offcomm[ind].reset_index(drop=True)
offcomm = offcomm[offcomm["lang"] == "en"].reset_index(drop=True)
offcomm.to_csv("data/preprocessed/officalCommFiltered.csv")
offcomm

id          date  \
0      1245440971896168448  1.585742e+09   
1      1245760292073672704  1.585819e+09   
2      1246075233208897544  1.585894e+09   
3      1246119052105453570  1.585904e+09   
4      1246203407674810368  1.585924e+09   
...                    ...           ...   
25176  1573676156255055872  1.664000e+09   
25177  1574003355604717570  1.664078e+09   
25178  1574694879430582273  1.664243e+09   
25179  1575102455364591616  1.664340e+09   
25180  1575392480773693441  1.664409e+09   

                                              rawContent  replyCount  \
0      Retirement community staff: Lower the chances ...           5   
1      The right message at the right time from the r...           9   
2      Everyone can help prevent spread of #COVID19. ...           3   
3      Do you have a loved one in a nursing home or a...           5   
4      #CareForEachOther by lending an ear (from a sa...           3   
...                                                  ...         ...   
25176  What does it mean when #polio virus is detecte...          64   
25177  If you plan to attend the @FIFAWorldCup in #Qa...          49   
25178  Second round of public hearings towards a #Pan...          32   
25179  This year, #WorldRabiesDay, let us bring toget...          49   
25180  🔴LIVE NOW - The second round of public hearing...          24   

       retweetCount  likeCount lang source sourceLabel viewCount  ...  \
0                32         38   en   None        None      None  ...   
1                42         67   en   None        None      None  ...   
2                61         70   en   None        None      None  ...   
3                37         48   en   None        None      None  ...   
4                23         43   en   None        None      None  ...   
...             ...        ...  ...    ...         ...       ...  ...   
25176           101        280   en   None        None      None  ...   
25177            51        153   en   None        None      None  ...   
25178            56        136   en   None        None      None  ...   
25179           170        467   en   None        None      None  ...   
25180            35         99   en   None        None      None  ...   

       userFriendsCount userStatusesCount  userFavouritesCount  \
0                   547             14916                 7997   
1                   547             14916                 7997   
2                   547             14916                 7997   
3                   547             14916                 7997   
4                   547             14916                 7997   
...                 ...               ...                  ...   
25176              1775             74644                12600   
25177              1775             74644                12600   
25178              1775             74644                12600   
25179              1775             74644                12600   
25180              1775             74644                12600   

      userListedCount userMediaCount         userLocation  userProtected  \
0               16382           4379          Atlanta, GA           None   
1               16382           4379          Atlanta, GA           None   
2               16382           4379          Atlanta, GA           None   
3               16382           4379          Atlanta, GA           None   
4               16382           4379          Atlanta, GA           None   
...               ...            ...                  ...            ...   
25176           35499          21839  Geneva, Switzerland           None   
25177           35499          21839  Geneva, Switzerland           None   
25178           35499          21839  Geneva, Switzerland           None   
25179           35499          21839  Geneva, Switzerland           None   
25180           35499          21839  Geneva, Switzerland           None   

                       userLink  userBlue  user

In [69]:
#calculate
offcomm = pd.read_csv("data/preprocessed/officalCommFiltered.csv")
offcomm = appendSentimentScore(offcomm,"rawContent", "offComm")
offcomm = appendVAD(offcomm,"rawContent", "offComm")
offcomm = appendFrequency(offcomm,"rawContent", "offComm")
offcomm = appendArousalScore(offcomm,"rawContent", "offComm")
offcomm = appendDominanceScore(offcomm,"rawContent", "offComm")
offcomm = appendConcretenessScore(offcomm,"rawContent", "offComm")
offcomm = appendGisPyData(offcomm, "offComm")
offcomm.to_csv("data/preprocessed/officalComm.csv")

C:\Users\chun_\AppData\Local\Temp\ipykernel_11352\950585433.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subResult["d_id"][i] = re.sub("^" + fileName +"_", "" ,subResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_11352\950585433.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subResult["d_id"][i] = re.sub(".txt*","",subResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_11352\950585433.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

# Preprocess Fake News

## Preprocess Covid Rumor

In [21]:
covidrumor = pd.read_csv("data/covidRumor/Twitter.csv")
covidrumor = appendSentimentScore(covidrumor,"content", "covidRumor")
covidrumor = appendVAD(covidrumor,"content", "covidRumor")
covidrumor = appendFrequency(covidrumor,"content", "covidRumor")
covidrumor = appendArousalScore(covidrumor,"content", "covidRumor")
covidrumor = appendDominanceScore(covidrumor,"content", "covidRumor")
covidrumor = appendConcretenessScore(covidrumor,"content", "covidRumor")
covidrumor = appendGisPyData(covidrumor, "covidRumor")
covidrumor.to_csv("data/preprocessed/covidRumor.csv")

covidrumor

C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gisPyResult["d_id"][i] = re.sub("^" + fileName +"_", "" ,gisPyResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gisPyResult["d_id"][i] = re.sub(".txt*","",gisPyResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide

No. label                                            content  \
0        1     F  If you can hold your breath without coughing, ...   
1        2     F  A homemade hand sanitizer made with Tito's Vod...   
2        3     F  Gargling with salt water or Vinegar 'eliminate...   
3        4     U  Patients should avoid taking ibuprofen to reli...   
4        5     F  Chinese officials are seeking approval to star...   
...    ...   ...                                                ...   
2700  2709     F  telecommunications services in the country wil...   
2701  2710     F  Gov. Steve Sisolak's activation of the Guard t...   
2702  2711     F                   An officer died from coronavirus   
2703  2712     F  National Guard is being mobilized for anything...   
2704  2713     T  Thank you for your leadership Mayor Lucas! My ...   

                   source sentiment  reply numbers  retweet numbers  \
0      850196512341262036         3            2.0             61.0   
1     8081445194953918218         3            3.0             41.0   
2     1803907737236930232         3            6.0             39.0   
3     1989310298994352163         3            0.0              0.0   
4     6967004759672387621         4            0.0              0.0   
...                   ...       ...            ...              ...   
2700  8183648438884397934         3            3.0              4.0   
2701  4396957800986667223         3            1.0              4.0   
2702  6356967677817419212         2            0.0              1.0   
2703  3111348880049192737         3            1.0              5.0   
2704  3418545398543234785   #VALUE!            0.0              3.0   

      likes numbers  sentiment_1  sentiment_2  ...  zSMCAUSwn_1p_binary  \
0              95.0     0.207285     0.279201  ...            -0.239914   
1              67.0     0.015723     0.018115  ...            -0.239914   
2              73.0     0.586720     0.235215  ...            -0.239914   
3               0.0     0.219345     0.262313  ...            -0.239914   
4               0.0     0.406963     0.229551  ...            -0.239914   
...             ...          ...          ...  ...                  ...   
2700            7.0     0.411384     0.377630  ...            -0.239914   
2701            3.0     0.267659     0.175939  ...            -0.239914   
2702            8.0     0.609838     0.197302  ...            -0.239914   
2703            5.0     0.469144     0.183379  ...            -0.239914   
2704           12.0     0.040590     0.031934  ...            -0.239914   

      zSMCAUSwn_ap_binary  zSMCAUSwn_1_binary  zSMCAUSwn_a_binary  \
0               -0.315127           -0.318678           -0.391433   
1               -0.315127           -0.318678           -0.391433   
2               -0.315127           -0.318678           -0.391433   
3               -0.315127           -0.318678           -0.391433   
4               -0.315127           -0.318678           -0.391433   
...                   ...                 ...                 ...   
2700            -0.315127           -0.318678           -0.391433   
2701            -0.315127           -0.318678           -0.391433   
2702            -0.315127           -0.318678           -0.391433   
2703            -0.315127           -0.318678           -0.391433   
2704            -0.315127           -0.318678           -0.391433   

      zPCCNC_megahr  zWRDIMGc_megahr  zPCCNC_mrc  zWRDIMGc_mrc  zWRDHYPnv  \
0         -0.298344        -0.350497    0.152589     -0.133736  -0.929958   
1          1.354302         1.251938    4.106812      3.888843  -0.520649   
2          1.930270         1.679579    3.297114      2.553089   1.218917   
3          0.488592         0.064175   -0.882797     -1.007941   0.693636   
4         -0.475926        -0.453767    0.522629      0.723974   0.080278   
...             ...              ...         ...           ...        ...   
2700       0.769342         0.04

## Preprocess Constraint@AAAI2021

In [68]:
constraintAAAI = pd.read_csv("data/constraintAAAI/Constraint_Train.csv", index_col = 0).reset_index()
constraintAAAI = appendSentimentScore(constraintAAAI,"tweet", "constraintAAAI")
constraintAAAI = appendVAD(constraintAAAI,"tweet", "constraintAAAI")
constraintAAAI = appendFrequency(constraintAAAI,"tweet", "constraintAAAI")
constraintAAAI = appendArousalScore(constraintAAAI,"tweet", "constraintAAAI")
constraintAAAI = appendDominanceScore(constraintAAAI,"tweet", "constraintAAAI")
constraintAAAI = appendConcretenessScore(constraintAAAI,"tweet", "constraintAAAI")
constraintAAAI = appendGisPyData(constraintAAAI, "constraintAAAI")
constraintAAAI.to_csv("data/preprocessed/constraintAAAI.csv")

constraintAAAI

C:\Users\chun_\AppData\Local\Temp\ipykernel_11352\950585433.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subResult["d_id"][i] = re.sub("^" + fileName +"_", "" ,subResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_11352\950585433.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subResult["d_id"][i] = re.sub(".txt*","",subResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_11352\950585433.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

id                                              tweet label  \
0        1  The CDC currently reports 99031 deaths. In gen...  real   
1        2  States reported 1121 deaths a small rise from ...  real   
2        3  Politically Correct Woman (Almost) Uses Pandem...  fake   
3        4  #IndiaFightsCorona: We have 1524 #COVID testin...  real   
4        5  Populous states can generate large case counts...  real   
...    ...                                                ...   ...   
6415  6416  A tiger tested positive for COVID-19 please st...  fake   
6416  6417  ???Autopsies prove that COVID-19 is??� a blood...  fake   
6417  6418  _A post claims a COVID-19 vaccine has already ...  fake   
6418  6419  Aamir Khan Donate 250 Cr. In PM Relief Cares Fund  fake   
6419  6420  It has been 93 days since the last case of COV...  real   

      sentiment_1  sentiment_2  sentiment_3  sentiment_4  sentiment_5  \
0        0.293009     0.348915     0.272724     0.065921     0.019431   
1        0.510309     0.236185     0.173387     0.055087     0.025031   
2        0.584950     0.240344     0.108160     0.045265     0.021282   
3        0.418822     0.196190     0.149308     0.115002     0.120677   
4        0.172136     0.265625     0.299878     0.167427     0.094933   
...           ...          ...          ...          ...          ...   
6415     0.651290     0.196761     0.085407     0.034860     0.031682   
6416     0.652602     0.250644     0.071785     0.015329     0.009641   
6417     0.617256     0.224270     0.097160     0.039639     0.021675   
6418     0.180699     0.105080     0.154739     0.237936     0.321547   
6419     0.392516     0.218098     0.117654     0.116647     0.155085   

       valence   arousal  ...  zSMCAUSwn_1p_binary  zSMCAUSwn_ap_binary  \
0     4.363846  4.043846  ...            -0.239914            -0.315127   
1     4.628571  4.208571  ...            10.686072             9.551547   
2     5.616000  3.536000  ...            -0.239914            -0.315127   
3     4.790000  4.340000  ...            -0.239914            -0.315127   
4     6.079231  4.096154  ...            -0.239914            -0.315127   
...        ...       ...  ...                  ...                  ...   
6415  6.702000  4.356000  ...            -0.239914            -0.315127   
6416  4.414000  4.253000  ...            -0.239914            -0.315127   
6417  5.386000  4.292000  ...            -0.239914            -0.315127   
6418  6.880000  3.732500  ...            -0.239914            -0.315127   
6419  5.337500  4.334167  ...            -0.239914            -0.315127   

      zSMCAUSwn_1_binary  zSMCAUSwn_a_binary  zPCCNC_megahr  zWRDIMGc_megahr  \
0              -0.318678           -0.391433       0.027565        -0.329632   
1               6.785653            7.903567       0.499695         0.265310   
2              -0.318678           -0.391433       1.069025         1.058496   
3              -0.318678           -0.391433       0.049484        -0.068945   
4              -0.318678           -0.391433       0.633136        -0.177163   
...                  ...                 ...            ...              ...   
6415           -0.318678           -0.391433       1.674748         2.101619   
6416           -0.318678           -0.391433      -0.507727        -0.183664   
6417           -0.318678           -0.391433      -1.461701        -1.914659   
6418           -0.318678           -0.391433       3.131256         2.671053   
6419           -0.318678           -0.391433      -0.919966        -1.165461   

      zPCCNC_mrc  zWRDIMGc_mrc  zWRDHYPnv       gis  
0      -0.417235     -0.152674  -0.544077  5.581378  
1      -1.465064     -1.525683  -0.929958 -3.797334  
2      -0.324104     -0.592144   1.227760 -4.740356  
3      -0.382721     -0.228321  -0.783026 -0.582587  
4      -1.836045     -1.928476  -0.102243 -2.125408  
...          ...           ...        ...       ...  
6415   -0.089371     -0.536671   1.132

In [26]:
covidrumor = pd.read_csv("data/covidRumor/Twitter.csv")
covidrumor = appendSentimentScore(covidrumor,"content","covidRumor")

covidrumor

No. label                                            content  \
0        1     F  If you can hold your breath without coughing, ...   
1        2     F  A homemade hand sanitizer made with Tito's Vod...   
2        3     F  Gargling with salt water or Vinegar 'eliminate...   
3        4     U  Patients should avoid taking ibuprofen to reli...   
4        5     F  Chinese officials are seeking approval to star...   
...    ...   ...                                                ...   
2700  2709     F  telecommunications services in the country wil...   
2701  2710     F  Gov. Steve Sisolak's activation of the Guard t...   
2702  2711     F                   An officer died from coronavirus   
2703  2712     F  National Guard is being mobilized for anything...   
2704  2713     T  Thank you for your leadership Mayor Lucas! My ...   

                   source sentiment  reply numbers  retweet numbers  \
0      850196512341262036         3            2.0             61.0   
1     8081445194953918218         3            3.0             41.0   
2     1803907737236930232         3            6.0             39.0   
3     1989310298994352163         3            0.0              0.0   
4     6967004759672387621         4            0.0              0.0   
...                   ...       ...            ...              ...   
2700  8183648438884397934         3            3.0              4.0   
2701  4396957800986667223         3            1.0              4.0   
2702  6356967677817419212         2            0.0              1.0   
2703  3111348880049192737         3            1.0              5.0   
2704  3418545398543234785   #VALUE!            0.0              3.0   

      likes numbers  Unnamed: 0  sentiment_1  sentiment_2  sentiment_3  \
0              95.0           0     0.207285     0.279201     0.275264   
1              67.0           1     0.015723     0.018115     0.086290   
2              73.0           2     0.586720     0.235215     0.077792   
3               0.0           3     0.219345     0.262313     0.256636   
4               0.0           4     0.406963     0.229551     0.158415   
...             ...         ...          ...          ...          ...   
2700            7.0        2700     0.411384     0.377630     0.156788   
2701            3.0        2701     0.267659     0.175939     0.197732   
2702            8.0        2702     0.609838     0.197302     0.109177   
2703            5.0        2703     0.469144     0.183379     0.148527   
2704           12.0        2704     0.040590     0.031934     0.074980   

      sentiment_4  sentiment_5  
0        0.161683     0.076568  
1        0.396360     0.483512  
2        0.057384     0.042888  
3        0.169155     0.092551  
4        0.125102     0.079969  
...           ...          ...  
2700     0.035404     0.018793  
2701     0.210114     0.148556  
2702     0.050047     0.033636  
2703     0.101941     0.097008  
2704     0.335656     0.516840  

[2705 rows x 14 columns]

In [9]:
coaid = pd.read_csv("NewsFakeCOVID-19_tweets.csv")["tweet_id"].to_list()

hydrateTweets(coaid, "data/coaid/", "data/failed/")

# for i in sntwitter.TwitterTweetScraper(1250073526700212230).get_items():
#     tweetToDict(i) 

Note: Tweets Deleted for1253279600119033856
Note: Tweets Deleted for1252271897850544131
Note: Tweets Deleted for1251308087467802624
Note: Tweets Deleted for1250628764431790080
Note: Tweets Deleted for1250256963251793921
Note: Tweets Deleted for1250211470295683072
Note: Tweets Deleted for1250148020341145600
Note: Tweets Deleted for1250144192677826560
Note: Tweets Deleted for1250143997089255424


Error retrieving https://twitter.com/i/api/graphql/miKSMGb2R1SewIJv2-ablQ/TweetDetail?variables=%7B%22focalTweetId%22%3A%221250142604538163200%22%2C%22with_rux_injections%22%3Afalse%2C%22includePromotedContent%22%3Atrue%2C%22withCommunity%22%3Atrue%2C%22withQuickPromoteEligibilityTweetFields%22%3Atrue%2C%22withBirdwatchNotes%22%3Afalse%2C%22withVoice%22%3Atrue%2C%22withV2Timeline%22%3Atrue%7D&features=%7B%22rweb_lists_timeline_redesign_enabled%22%3Afalse%2C%22blue_business_profile_image_shape_enabled%22%3Atrue%2C%22responsive_web_graphql_exclude_directive_enabled%22%3Atrue%2C%22verified_phone_label_enabled%22%3Afalse%2C%22creator_subscriptions_tweet_preview_api_enabled%22%3Afalse%2C%22responsive_web_graphql_timeline_navigation_enabled%22%3Atrue%2C%22responsive_web_graphql_skip_user_profile_image_extensions_enabled%22%3Afalse%2C%22tweetypie_unmention_optimization_enabled%22%3Atrue%2C%22vibe_api_enabled%22%3Atrue%2C%22responsive_web_edit_tweet_api_enabled%22%3Atrue%2C%22graphql_is_transl

Note: Tweets Result Error for1250142604538163200
Note: Tweets Deleted for1250073526700212230
Note: Tweets Deleted for1250070553710469122
Note: Tweets Deleted for1250029387325603840
Note: Tweets Deleted for1250006323028267008
Note: Tweets Deleted for1249783029213605888
Note: Tweets Deleted for1249781738567544834
Note: Tweets Deleted for1249567153189257217
Note: Tweets Deleted for1249563905220694018
Note: Tweets Deleted for1249487651482341376
Note: Tweets Deleted for1249481937124651008


Error retrieving https://twitter.com/i/api/graphql/miKSMGb2R1SewIJv2-ablQ/TweetDetail?variables=%7B%22focalTweetId%22%3A%221249416698320519169%22%2C%22with_rux_injections%22%3Afalse%2C%22includePromotedContent%22%3Atrue%2C%22withCommunity%22%3Atrue%2C%22withQuickPromoteEligibilityTweetFields%22%3Atrue%2C%22withBirdwatchNotes%22%3Afalse%2C%22withVoice%22%3Atrue%2C%22withV2Timeline%22%3Atrue%7D&features=%7B%22rweb_lists_timeline_redesign_enabled%22%3Afalse%2C%22blue_business_profile_image_shape_enabled%22%3Atrue%2C%22responsive_web_graphql_exclude_directive_enabled%22%3Atrue%2C%22verified_phone_label_enabled%22%3Afalse%2C%22creator_subscriptions_tweet_preview_api_enabled%22%3Afalse%2C%22responsive_web_graphql_timeline_navigation_enabled%22%3Atrue%2C%22responsive_web_graphql_skip_user_profile_image_extensions_enabled%22%3Afalse%2C%22tweetypie_unmention_optimization_enabled%22%3Atrue%2C%22vibe_api_enabled%22%3Atrue%2C%22responsive_web_edit_tweet_api_enabled%22%3Atrue%2C%22graphql_is_transl

Note: Tweets Result Error for1249416698320519169
Note: Tweets Deleted for1249413181254127616
Note: Tweets Deleted for1249409301795528713
Note: Tweets Deleted for1249401909917749248
Note: Tweets Deleted for1249400432864059392
Note: Tweets Deleted for1249400042080829445
Note: Tweets Deleted for1249393236759711745
Note: Tweets Deleted for1249391598439485445
Note: Tweets Deleted for1249388266916319232
Note: Tweets Deleted for1249372688080084993
Note: Tweets Deleted for1249369470507892736
Note: Tweets Deleted for1249368712198721537
Note: Tweets Deleted for1249367400425848832


...

Note: Tweets Result Error for1223638980572237827


Error retrieving https://twitter.com/i/api/graphql/miKSMGb2R1SewIJv2-ablQ/TweetDetail?variables=%7B%22focalTweetId%22%3A%221223638960418758656%22%2C%22with_rux_injections%22%3Afalse%2C%22includePromotedContent%22%3Atrue%2C%22withCommunity%22%3Atrue%2C%22withQuickPromoteEligibilityTweetFields%22%3Atrue%2C%22withBirdwatchNotes%22%3Afalse%2C%22withVoice%22%3Atrue%2C%22withV2Timeline%22%3Atrue%7D&features=%7B%22rweb_lists_timeline_redesign_enabled%22%3Afalse%2C%22blue_business_profile_image_shape_enabled%22%3Atrue%2C%22responsive_web_graphql_exclude_directive_enabled%22%3Atrue%2C%22verified_phone_label_enabled%22%3Afalse%2C%22creator_subscriptions_tweet_preview_api_enabled%22%3Afalse%2C%22responsive_web_graphql_timeline_navigation_enabled%22%3Atrue%2C%22responsive_web_graphql_skip_user_profile_image_extensions_enabled%22%3Afalse%2C%22tweetypie_unmention_optimization_enabled%22%3Atrue%2C%22vibe_api_enabled%22%3Atrue%2C%22responsive_web_edit_tweet_api_enabled%22%3Atrue%2C%22graphql_is_transl

Note: Tweets Result Error for1223638960418758656
Note: Tweets Deleted for1223637495998550017
Note: Tweets Deleted for1223636357618204672


Error retrieving https://twitter.com/i/api/graphql/miKSMGb2R1SewIJv2-ablQ/TweetDetail?variables=%7B%22focalTweetId%22%3A%221223635771770404864%22%2C%22with_rux_injections%22%3Afalse%2C%22includePromotedContent%22%3Atrue%2C%22withCommunity%22%3Atrue%2C%22withQuickPromoteEligibilityTweetFields%22%3Atrue%2C%22withBirdwatchNotes%22%3Afalse%2C%22withVoice%22%3Atrue%2C%22withV2Timeline%22%3Atrue%7D&features=%7B%22rweb_lists_timeline_redesign_enabled%22%3Afalse%2C%22blue_business_profile_image_shape_enabled%22%3Atrue%2C%22responsive_web_graphql_exclude_directive_enabled%22%3Atrue%2C%22verified_phone_label_enabled%22%3Afalse%2C%22creator_subscriptions_tweet_preview_api_enabled%22%3Afalse%2C%22responsive_web_graphql_timeline_navigation_enabled%22%3Atrue%2C%22responsive_web_graphql_skip_user_profile_image_extensions_enabled%22%3Afalse%2C%22tweetypie_unmention_optimization_enabled%22%3Atrue%2C%22vibe_api_enabled%22%3Atrue%2C%22responsive_web_edit_tweet_api_enabled%22%3Atrue%2C%22graphql_is_transl

Note: Tweets Result Error for1223635771770404864
Note: Tweets Deleted for1223635533655609345
Note: Tweets Deleted for1223635286544003074


In [12]:
def compileHydratedData(directory):
    returnValue = pd.DataFrame()
    for filename in os.listdir(directory):
        f = os.path.join(directory, filename)
        if os.path.isdir(f):
            returnValue = pd.concat([returnValue, compileHydratedData(f)]) ##
        else:
            jsonDict = json.load(open(f))
            returnValue = pd.concat([returnValue, pd.DataFrame([[jsonDict[i] for i in jsonDict]], columns = [i for i in jsonDict]) ])
    return returnValue

coaid = compileHydratedData("data\\coaid").reset_index(drop=True)
coaid.to_csv("data/preprocessed/coaid_NoFeature.csv")

In [19]:
for i in coaid["rawContent"]:
    print(i)

🤔 Bill and Melinda Gates Foundation &amp; Others Predicted Up To 65 Million Deaths Via Coronavirus – In Simulation Ran 3 Months Ago! https://t.co/EIILRnmxfU
Bill and Melinda Gates Foundation &amp; Others Predicted Up To 65 Million Deaths Via Coronavirus – In Simulation Ran 3 Months Ago! https://t.co/rm3Wss7NVS
@ConflictsW @Lealokkk @Global_Mil_Info @DewsNewz @ISCResearch @CNN @DrTedros @PolishPatriotTM @OffLimitsNews Bill and Melinda Gates Foundation &amp; Others Predicted Up To 65 Million Deaths Via Coronavirus – In Simulation Ran 3 Months Ago!

Millie Weaver @Millie__Weaver

#CoronaVirus
#WuhanFlu
#2019nCoV

https://t.co/hTFnxfrQ8I
Bill and Melinda Gates Foundation &amp; Others Predicted Up To 65 Million Deaths Via Coronavirus – In Simulation Ran 3 Months Ago! https://t.co/N6ILLvNiyc
Bill and Melinda Gates Foundation &amp; Others Predicted Up To 65 Million Deaths Via Coronavirus – In Simulation Ran 3 Months Ago! https://t.co/wTKyn9e8rV
Is being a Psychopath also a prerequisite to bei

In [29]:
coaid = pd.read_csv("data/preprocessed/coaid_NoFeature.csv")
coaid = appendSentimentScore(coaid,"rawContent", "coaid")
coaid = appendVAD(coaid,"rawContent", "coaid")
coaid = appendFrequency(coaid,"rawContent", "coaid")
coaid = appendArousalScore(coaid,"rawContent", "coaid")
coaid = appendDominanceScore(coaid,"rawContent", "coaid")
coaid = appendConcretenessScore(coaid,"rawContent", "coaid")
coaid = appendGisPyData(coaid, "coaid")
coaid.to_csv("data/preprocessed/coaid.csv")
coaid

C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gisPyResult["d_id"][i] = re.sub("^" + fileName +"_", "" ,gisPyResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gisPyResult["d_id"][i] = re.sub(".txt*","",gisPyResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide

Unnamed: 0                   id          date  \
0              0  1220495593497399298  1.579824e+09   
1              1  1220495745897435136  1.579824e+09   
2              2  1220496382940925952  1.579824e+09   
3              3  1220497176419135488  1.579824e+09   
4              4  1220498430201491456  1.579824e+09   
...          ...                  ...           ...   
5496        5496  1256280854931931140  1.588352e+09   
5497        5497  1256291122600644609  1.588355e+09   
5498        5498  1256305644346302465  1.588358e+09   
5499        5499  1256341742032490497  1.588367e+09   
5500        5500  1256365547320729604  1.588372e+09   

                                             rawContent  replyCount  \
0     🤔 Bill and Melinda Gates Foundation &amp; Othe...           0   
1     Bill and Melinda Gates Foundation &amp; Others...          27   
2     @ConflictsW @Lealokkk @Global_Mil_Info @DewsNe...           1   
3     Bill and Melinda Gates Foundation &amp; Others...           0   
4     Bill and Melinda Gates Foundation &amp; Others...           0   
...                                                 ...         ...   
5496  Lab-Made Coronavirus Triggers Debate https://t...           0   
5497  Lab-Made Coronavirus Triggers Debate https://t...           0   
5498  @AnneTorppa @SuskuLondon Flu Vaccine Increases...           1   
5499  @JodieMoss76 @Acosta @PressSec Or what about S...           0   
5500  @WRAL @NC_Governor\n@RoyCooperNC\n@SecMandyCoh...           0   

      retweetCount  likeCount lang  source  sourceLabel  ...  \
0                3          4   en     NaN          NaN  ...   
1               86        115   en     NaN          NaN  ...   
2                2          2   en     NaN          NaN  ...   
3                0          0   en     NaN          NaN  ...   
4                0          0   en     NaN          NaN  ...   
...            ...        ...  ...     ...          ...  ...   
5496             0          0   ca     NaN          NaN  ...   
5497             0          0   ca     NaN          NaN  ...   
5498             0          5   en     NaN          NaN  ...   
5499             0          1   en     NaN          NaN  ...   
5500             0          0   ca     NaN          NaN  ...   

      zSMCAUSwn_1p_binary  zSMCAUSwn_ap_binary  zSMCAUSwn_1_binary  \
0               -0.070296             -0.11827           -0.101612   
1               -0.070296             -0.11827           -0.101612   
2               -0.070296             -0.11827           -0.101612   
3               -0.070296             -0.11827           -0.101612   
4               -0.070296             -0.11827           -0.101612   
...                   ...                  ...                 ...   
5496            -0.070296             -0.11827           -0.101612   
5497            -0.070296             -0.11827           -0.101612   
5498            -0.070296             -0.11827           -0.101612   
5499            -0.070296             -0.11827           -0.101612   
5500            -0.070296             -0.11827           -0.101612   

      zSMCAUSwn_a_binary zPCCNC_megahr zWRDIMGc_megahr  zPCCNC_mrc  \
0              -0.135771      0.828164        0.376861   -0.085945   
1              -0.135771      0.828164        0.376861   -0.085945   
2              -0.135771      1.485002        1.063136   -0.461758   
3              -0.135771      0.828164        0.376861   -0.085945   
4              -0.135771      0.212796        0.017283   -0.010783   
...                  ...           ...             ...         ...   
5496           -0.135771      1.777762        1.057169    0.807823   
5497           -0.135771      1.777762        1.057169    0.807823   
5498           -0.135771     -0.301324       -0.599153   -0.986945   
5499           -0.135771     -0.317542        0.221745    0.326758   
5500           -0.135771      2.064361        1.251111    0.220413   

      zWRDIMGc_mrc  zWRDHYPnv       gis  

In [30]:
coaid["MedianContentRank"]

0        4286.0
1        4286.0
2        4959.0
3        4286.0
4        4301.5
         ...   
5496    15838.0
5497    15838.0
5498     2293.0
5499     4554.0
5500    65780.0
Name: MedianContentRank, Length: 5501, dtype: float64

In [24]:
truthseeker = pd.read_csv("data/Truth_Seeker_Model_Dataset.csv", index_col = 0)
truthseeker = truthseeker[[isCovidRelated(keywords) for keywords in truthseeker["manual_keywords"]]].reset_index(drop = True)
truthseeker.to_csv("data/preprocessed/truthseeker_NoFeature.csv")
len(truthseeker)

14379

In [60]:
def isCovidRelated(text):
    return len(re.findall((".*(covid|corona|demic|quarantin| case| test|virus|vaccin|spread).*"), text.lower())) > 0
emptyDocument()
AddDocumentTofolder(truthseeker["tweet"], "truthseeker")

In [26]:
truthseeker = pd.read_csv("data/preprocessed/truthseeker_NoFeature.csv", index_col = 0)
truthseeker = appendSentimentScore(truthseeker,"tweet", "truthseeker")
truthseeker = appendVAD(truthseeker,"tweet", "truthseeker")
truthseeker = appendFrequency(truthseeker,"tweet", "truthseeker")
truthseeker = appendArousalScore(truthseeker,"tweet", "truthseeker")
truthseeker = appendDominanceScore(truthseeker,"tweet", "truthseeker")
truthseeker = appendConcretenessScore(truthseeker,"tweet", "truthseeker")
truthseeker = appendGisPyData(truthseeker, "truthseeker")
truthseeker.to_csv("data/preprocessed/truthseeker.csv")
truthseeker

C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gisPyResult["d_id"][i] = re.sub("^" + fileName +"_", "" ,gisPyResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gisPyResult["d_id"][i] = re.sub(".txt*","",gisPyResult["d_id"][i])
C:\Users\chun_\AppData\Local\Temp\ipykernel_16232\987537876.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide

author                                          statement  target  \
0      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
1      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
2      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
3      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
4      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
...            ...                                                ...     ...   
14374   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14375   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14376   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14377   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14378   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   

       BinaryNumTarget                                 manual_keywords  \
0                  1.0              Florida, COVID-19, patients, floor   
1                  1.0              Florida, COVID-19, patients, floor   
2                  1.0              Florida, COVID-19, patients, floor   
3                  1.0              Florida, COVID-19, patients, floor   
4                  1.0              Florida, COVID-19, patients, floor   
...                ...                                             ...   
14374              0.0  cases are going up, because, testing, going up   
14375              0.0  cases are going up, because, testing, going up   
14376              0.0  cases are going up, because, testing, going up   
14377              0.0  cases are going up, because, testing, going up   
14378              0.0  cases are going up, because, testing, going up   

                                                   tweet  \
0      A photo showing COVID-19 patients lying on the...   
1      My fraternity brother who is a critical care p...   
2      Just makes the ballot harvesting seem so ... p...   
3      @realDonaldTrump Mr. President, This info will...   
4      @gcraige Big Lies!!! I Live In Florida, These ...   
...                                                  ...   
14374  @HiMyNameIsSeton @dpshow @peter_king Not sure ...   
14375  Still going with the classic cases are up beca...   
14376  @4446Mark Cases are going up in the U.S. becau...   
14377  @realDonaldTrump @EveningEdit Pretty simple ki...   
14378  Trump one year ago today: Cases are going up i...   

      5_label_majority_answer 3_label_majority_answer  sentiment_1  \
0                       Agree                   Agree     0.493554   
1                Mostly Agree                   Agree     0.088281   
2                Mostly Agree                   Agree     0.188830   
3                       Agree                   Agree     0.826044   
4                       Agree                   Agree     0.595326   
...                       ...                     ...          ...   
14374                   Agree                   Agree     0.238181   
14375                   Agree                   Agree     0.002342   
14376            Mostly Agree                   Agree     0.038868   
14377                   Agree                   Agree     0.127606   
14378            Mostly Agree                   Agree     0.087523   

       sentiment_2  ...  zSMCAUSwn_1p_binary  zSMCAUSwn_ap_binary  \
0         0.262117  ...            -0.340933            -0.423045   
1         0.052049  ...            -0.340933            -0.423045   
2         0.358386  ...            -0.340933            -0.423045   
3         0.089252  ...             0.769243            -0.024570   
4         0.219537  ...            -0.340933            -0.423045   
...            ...  ...                  ...                  ...   
14374     0.408409  ...            -0.340933            -0.423045   
14375     0.004740  ...            -

In [27]:
truthseeker

author                                          statement  target  \
0      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
1      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
2      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
3      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
4      Amy Sherman  A photo shows two COVID-19 patients lying on t...    True   
...            ...                                                ...     ...   
14374   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14375   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14376   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14377   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   
14378   Eric Litke  The (COVID-19) cases are going up, but it's be...   False   

       BinaryNumTarget                                 manual_keywords  \
0                  1.0              Florida, COVID-19, patients, floor   
1                  1.0              Florida, COVID-19, patients, floor   
2                  1.0              Florida, COVID-19, patients, floor   
3                  1.0              Florida, COVID-19, patients, floor   
4                  1.0              Florida, COVID-19, patients, floor   
...                ...                                             ...   
14374              0.0  cases are going up, because, testing, going up   
14375              0.0  cases are going up, because, testing, going up   
14376              0.0  cases are going up, because, testing, going up   
14377              0.0  cases are going up, because, testing, going up   
14378              0.0  cases are going up, because, testing, going up   

                                                   tweet  \
0      A photo showing COVID-19 patients lying on the...   
1      My fraternity brother who is a critical care p...   
2      Just makes the ballot harvesting seem so ... p...   
3      @realDonaldTrump Mr. President, This info will...   
4      @gcraige Big Lies!!! I Live In Florida, These ...   
...                                                  ...   
14374  @HiMyNameIsSeton @dpshow @peter_king Not sure ...   
14375  Still going with the classic cases are up beca...   
14376  @4446Mark Cases are going up in the U.S. becau...   
14377  @realDonaldTrump @EveningEdit Pretty simple ki...   
14378  Trump one year ago today: Cases are going up i...   

      5_label_majority_answer 3_label_majority_answer  sentiment_1  \
0                       Agree                   Agree     0.493554   
1                Mostly Agree                   Agree     0.088281   
2                Mostly Agree                   Agree     0.188830   
3                       Agree                   Agree     0.826044   
4                       Agree                   Agree     0.595326   
...                       ...                     ...          ...   
14374                   Agree                   Agree     0.238181   
14375                   Agree                   Agree     0.002342   
14376            Mostly Agree                   Agree     0.038868   
14377                   Agree                   Agree     0.127606   
14378            Mostly Agree                   Agree     0.087523   

       sentiment_2  ...  zSMCAUSwn_1p_binary  zSMCAUSwn_ap_binary  \
0         0.262117  ...            -0.340933            -0.423045   
1         0.052049  ...            -0.340933            -0.423045   
2         0.358386  ...            -0.340933            -0.423045   
3         0.089252  ...             0.769243            -0.024570   
4         0.219537  ...            -0.340933            -0.423045   
...            ...  ...                  ...                  ...   
14374     0.408409  ...            -0.340933            -0.423045   
14375     0.004740  ...            -

In [ ]:
#use regex to find cases: 14371/14379